#### 뉴스 기사 자연어 처리 분류모델 구현
- 2024-10-09 시행
- 데이터셋 : 200개 한국어 뉴스기사
- 라 벨 : 정치(0), 경제(1), 사회(2), 생활/문화(3), 세계(4), 기술/IT(5), 연예(6), 스포츠(7)
- 입력 받은 TEXT에 대한 기사 종류 분류 결과 출력하기
<hr>

[1] 폴더에서 뉴스파일 읽어오기 <hr>

In [1]:
import os

# 뉴스 카테고리 폴더 경로
dataset_dir = r"C:\Users\kimjaesung\9.자연어처리\nltk_project\nltkText_Dataset"

# 각 폴더의 카테고리 이름 (0: 정치, 1: 경제, ...)
categories = ['정치', '경제', '사회', '생활/문화', '세계', '기술/IT', '연예', '스포츠']

# 뉴스를 저장할 리스트
news_data = []

# 각 폴더에서 텍스트 파일 읽기
for category_id, category_name in enumerate(categories):
    category_path = os.path.join(dataset_dir, str(category_id))
    
    # 폴더 내의 파일을 순회하며 읽음
    for file_name in os.listdir(category_path):
        file_path = os.path.join(category_path, file_name)
        with open(file_path, 'r', encoding='utf-8') as f:
            content = f.read()
            # 뉴스 내용과 카테고리 정보를 저장
            news_data.append((content, category_name))

# 데이터 확인
print(news_data[:5])  # 첫 5개의 뉴스 기사와 카테고리 출력



[('동남아 담당\' 北 최희철 부상 베이징 도착…싱가포르행 주목\t최 부상, 행선지·방문 목적 질문에는 \'묵묵부답\'\n\n(베이징=연합뉴스) 김진방 특파원 = 북한이 북미 정상회담 무산 가능성까지 거론하며 강경한 태도를 보이는 가운데 동남아시아 외교를 담당하는 최희철 북한 외무성 부상이 19일 중국 베이징 서우두(首都) 공항에 모습을 드러냈다.\n\n최 부상은 이날 오전 평양발 고려항공 JS151편을 이용해 베이징 서우두 공항에 도착했다.\n\n최 부상은 최종 목적지를 묻는 취재진의 질문에 아무런 답변을 하지 않고, 북한 대사관 관계자들과 함께 공항을 빠져나갔다.\n\n북미 정상회담을 20여 일 앞둔 상황에서 동남아 외교통인 최 부상이 정상회담 준비 등을 위해 회담 개최 예정지인 싱가포르를 방문할 가능성도 제기되고 있다.\n\n최 부상은 지난 3월에도 아세안(ASEAN·동남아시아국가연합) 의장국이기도 한 싱가포르를 방문해 양국관계와 올해 8월 열리는 아세안지역안보포럼(ARF) 의제 등을 논의한 바 있다.\n\n또 지난해 북핵 문제를 두고 북미 간 긴장관계가 형성됐을 때도 ARF에 참석해 아세안을 상대로 여론전을 펼쳤다. 북한의 초청으로 비자이 쿠마르 싱 인도 외교부 국무장관이 방북했을 때도 최 부상은 싱 국무장관을 직접 영접하고, 한반도 문제를 논의하기도 했다.\n\n베이징 소식통은 "최 부상이 대(對)미 외교담당이 아니기 때문에 싱가포르로 갈 가능성이 큰 것은 아니다"며 "만약 싱가포르에 간다면 정상회담과 관련한 지원 작업 준비 등을 위한 것일 가능성이 크다"고 말했다.', '정치'), ('예결위, 추경 막바지 심사 진통…여야 충돌\t(서울=연합뉴스) 김남권 기자 = 국회 예산결산특별위원회는 19일 추가경정예산안의 막바지 심사에 돌입했으나 여야 간 이견에 진통을 겪고 있다. \n\n예결위는 이날 오전 8시 소소위원회를 열고 전날까지 심사에서 보류된 사업 53건의 감액 심사를 했다. \n\n여야 4개 교섭단체의 예결위 간사들만 참석하는 소소위는 심사한 지

[2] 텍스트 데이터 전처리하기 <hr>

In [6]:
from konlpy.tag import Okt
import re



# 형태소 분석기
okt = Okt()

# 불용어 리스트
stopwords = [
    # 기존에 사용 중인 불용어 리스트
    '이', '그', '저', '것', '들', '에서', '이다', '있다', '합니다', '했는데', '그리고',
    
    # 추가 불용어
    # 동사/형용사
    '하다', '되다', '있다', '없다', '되다', '나오다', '가다', '오다', '보다', '알다', '말하다', 
    '같다', '어떻다', '때문에', '통해', '따르다', '관련하다', '대하다', '만들다', '사용하다', 
    
    # 기능어 (조사, 접속사 등)
    '과', '도', '는', '다시', '또는', '그리고', '그러나', '이후', '지금', '경우', '등', '앞서',
    '통해', '위해', '동안', '더욱', '뿐만', '중', '많이', '대해', '하지만', '그러나', '이같이', 
    
    # 뉴스 기사에서 자주 나오는 표현
    '기자', '보도', '언론', '뉴스', '인터뷰', '보도자료', '방송', '중계', '기사', '제공',
    
    # 시간 관련 단어
    '년', '월', '일', '시간', '분', '초', '이번', '지난', '현재', '금년', '올해', '최근',
    
    # 기타
    '따라서', '또한', '결국', '대부분', '하지만', '때문에', '모든', '이상', '이후', '이전', 
]


# 전처리 함수
def preprocess(text):
    # 특수문자 제거
    text = re.sub(r"[^ㄱ-ㅎㅏ-ㅣ가-힣 ]", "", text)
    
    # 형태소 분석 및 어간 추출
    tokens = okt.morphs(text, stem=True)
    
    # 불용어 제거
    tokens = [word for word in tokens if word not in stopwords]
    
    return tokens

# 뉴스 데이터를 전처리
processed_news_data = [(preprocess(content), category) for content, category in news_data]

# 전처리 결과 확인
print(processed_news_data[:])  # 첫 5개의 전처리된 뉴스 기사와 카테고리 출력


[(['동남아', '담당', '최희', '철', '부상', '베이징', '도착', '싱가포르', '행', '주목', '최', '부상', '행선', '지', '방문', '목적', '질문', '에는', '묵묵', '부다', '베이징', '연합뉴스', '김진', '방', '특파원', '북한', '북미', '정상회담', '무산', '가능성', '까지', '거론', '강경하다', '태도', '를', '보이다', '가운데', '동남아시아', '외교', '를', '담당', '최희', '철', '북한', '외무성', '부상', '중국', '베이징', '서우', '두', '공항', '에', '모습', '을', '드러내다', '최', '부상', '은', '날', '오전', '평양', '발', '고려항공', '편', '을', '이용', '베이징', '서우', '두', '공항', '에', '도착', '최', '부상', '은', '최종', '목적지', '를', '묻다', '취재', '진의', '질문', '에', '아무렇다', '답변', '을', '않다', '북한', '대사관', '관계자', '함께', '공항', '을', '빠져나가다', '북미', '정상회담', '을', '여', '앞두다', '상황', '동남아', '외교', '통인', '최', '부상', '정상회담', '준비', '을', '회담', '개최', '예', '정지인', '싱가포르', '를', '방문', '가능성', '제기', '최', '부상', '은', '에도', '아세안', '동남아시아', '국가연합', '의장', '국', '이기도', '싱가포르', '를', '방문', '양국', '관계', '와', '열리다', '아세안', '지역', '안보', '포럼', '의제', '을', '논의', '한', '바', '또', '지난해', '북핵', '문제', '를', '두다', '북미', '간', '긴장', '관계', '가', '형성', '돼다', '때', '에', '참석', '아세안', '을', '상대로', '여론', '전', '을'

In [7]:
print(processed_news_data[:])

[(['동남아', '담당', '최희', '철', '부상', '베이징', '도착', '싱가포르', '행', '주목', '최', '부상', '행선', '지', '방문', '목적', '질문', '에는', '묵묵', '부다', '베이징', '연합뉴스', '김진', '방', '특파원', '북한', '북미', '정상회담', '무산', '가능성', '까지', '거론', '강경하다', '태도', '를', '보이다', '가운데', '동남아시아', '외교', '를', '담당', '최희', '철', '북한', '외무성', '부상', '중국', '베이징', '서우', '두', '공항', '에', '모습', '을', '드러내다', '최', '부상', '은', '날', '오전', '평양', '발', '고려항공', '편', '을', '이용', '베이징', '서우', '두', '공항', '에', '도착', '최', '부상', '은', '최종', '목적지', '를', '묻다', '취재', '진의', '질문', '에', '아무렇다', '답변', '을', '않다', '북한', '대사관', '관계자', '함께', '공항', '을', '빠져나가다', '북미', '정상회담', '을', '여', '앞두다', '상황', '동남아', '외교', '통인', '최', '부상', '정상회담', '준비', '을', '회담', '개최', '예', '정지인', '싱가포르', '를', '방문', '가능성', '제기', '최', '부상', '은', '에도', '아세안', '동남아시아', '국가연합', '의장', '국', '이기도', '싱가포르', '를', '방문', '양국', '관계', '와', '열리다', '아세안', '지역', '안보', '포럼', '의제', '을', '논의', '한', '바', '또', '지난해', '북핵', '문제', '를', '두다', '북미', '간', '긴장', '관계', '가', '형성', '돼다', '때', '에', '참석', '아세안', '을', '상대로', '여론', '전', '을'

[3] 단어 사전 만들기 <hr>

In [3]:
from collections import Counter

# 전처리된 뉴스 데이터에서 모든 단어를 모아 단어 빈도 계산
all_tokens = [word for tokens, _ in processed_news_data for word in tokens]
word_counter = Counter(all_tokens)

# 단어 사전 생성 (빈도수가 높은 단어부터 인덱스를 부여)
word_to_id = {word: i for i, (word, _) in enumerate(word_counter.most_common(), 1)}  # 인덱스 1부터 시작

# 단어 사전 상위 10개 출력
print(list(word_to_id.items())[:10])

# 토큰화된 문장을 단어 사전을 이용해 정수 인덱스로 변환
tokenized_data = [[word_to_id[word] for word in tokens if word in word_to_id] for tokens, _ in processed_news_data]

# 첫 5개의 토큰화된 결과 출력
print(tokenized_data[:5])


[('을', 1), ('에', 2), ('의', 3), ('를', 4), ('은', 5), ('가', 6), ('으로', 7), ('한', 8), ('로', 9), ('수', 10)]
[[5386, 1040, 13102, 3205, 721, 1070, 1369, 1205, 3574, 709, 402, 721, 4217, 56, 568, 1460, 507, 32, 6602, 2721, 1070, 149, 5387, 1071, 983, 35, 148, 135, 2074, 146, 22, 1754, 3712, 1206, 4, 57, 246, 9655, 739, 4, 1040, 13102, 3205, 35, 2498, 721, 50, 1070, 11025, 73, 1207, 2, 147, 1, 886, 402, 721, 5, 33, 209, 1461, 1015, 8670, 1311, 1, 185, 1070, 11025, 73, 1207, 2, 1369, 402, 721, 5, 569, 7832, 4, 1119, 762, 3018, 507, 2, 2363, 1793, 1, 15, 35, 1833, 78, 71, 1207, 1, 2912, 148, 135, 1, 189, 410, 84, 5386, 739, 13103, 402, 721, 135, 324, 1, 123, 297, 631, 16665, 1205, 4, 568, 146, 377, 402, 721, 5, 90, 6603, 9655, 13104, 1187, 453, 2301, 1205, 4, 568, 1939, 253, 12, 103, 6603, 110, 1349, 3713, 4218, 1, 363, 8, 283, 68, 75, 1901, 67, 4, 266, 148, 101, 1868, 253, 6, 1610, 14, 42, 2, 529, 6603, 1, 784, 1562, 18, 1, 899, 35, 3, 1719, 7, 7139, 16666, 7833, 9656, 1041, 2364, 3318, 2302, 4

[4] 패딩 후 LSTM/GRU 모델을 사용하여 다중 분류 학습 시행 <hr>

In [ ]:
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.utils.rnn as rnn_utils
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score, precision_score, recall_score
from sklearn.preprocessing import LabelEncoder
import numpy as np
from sklearn.utils.class_weight import compute_class_weight

# 1. 패딩 적용
def pad_sequences(tokenized_data, max_len=None):
    if not max_len:
        max_len = max(len(seq) for seq in tokenized_data)  # 문서 중 가장 긴 길이를 max_len으로 설정
    padded_data = rnn_utils.pad_sequence(
        [torch.tensor(seq) for seq in tokenized_data], 
        batch_first=True, 
        padding_value=0  # 패딩을 위한 값 (보통 0)
    )
    return padded_data

# 토큰화된 데이터를 패딩 처리
padded_data = pad_sequences(tokenized_data)
print("패딩된 데이터 크기:", padded_data.shape)

# 2. GRU 모델 구성 (다중 분류)
class RNNClassifier(nn.Module):
    def __init__(self, n_vocab, embedding_dim, hidden_dim, n_layers, n_classes, dropout=0.2, rnn_type="gru"):
        super(RNNClassifier, self).__init__()

        # 임베딩 레이어 (단어를 고정된 차원의 벡터로 변환)
        self.embedding = nn.Embedding(num_embeddings=n_vocab, embedding_dim=embedding_dim, padding_idx=0)

        # GRU 레이어 구성 (양방향, 3 레이어)
        if rnn_type == "gru":
            self.rnn = nn.GRU(input_size=embedding_dim, hidden_size=hidden_dim, num_layers=n_layers, 
                              bidirectional=True, dropout=dropout, batch_first=True)

        # 분류 레이어 (카테고리 수만큼 출력)
        self.fc = nn.Linear(hidden_dim * 2, n_classes)  # 양방향이므로 hidden_dim * 2

        # 드롭아웃 적용
        self.dropout = nn.Dropout(dropout)

    def forward(self, inputs):
        embedded = self.embedding(inputs)  # (배치 크기, 문장 길이, 임베딩 차원)
        output, _ = self.rnn(embedded)  # GRU의 출력
        last_hidden = self.dropout(output[:, -1, :])  # 마지막 타임스텝의 출력 (배치 크기, hidden_dim * 2)
        logits = self.fc(last_hidden)  # 다중 클래스 분류를 위한 출력
        return logits

# 3. 가중치 초기화 함수 추가
def init_weights(m):
    if isinstance(m, nn.Linear):
        nn.init.xavier_uniform_(m.weight)
    elif isinstance(m, nn.Embedding):
        nn.init.uniform_(m.weight, -0.1, 0.1)
    elif isinstance(m, (nn.LSTM, nn.GRU)):
        for name, param in m.named_parameters():
            if 'weight' in name:
                nn.init.xavier_uniform_(param)

# 4. 손실 함수 및 옵티마이저 정의

# 단어 사전 크기 및 하이퍼파라미터 설정
n_vocab = len(word_to_id) + 1  # 단어 사전 크기 (+1은 패딩을 위한 공간)
embedding_dim = 256  # 임베딩 차원 (256으로 증가)
hidden_dim = 128  # 은닉층 크기 (128로 증가)
n_layers = 3  # 레이어 수 (3으로 증가)
n_classes = len(categories)  # 뉴스 카테고리 수
dropout = 0.2  # 드롭아웃 비율

# 모델 생성 (GRU 적용)
device = "cuda" if torch.cuda.is_available() else "cpu"
model = RNNClassifier(n_vocab, embedding_dim, hidden_dim, n_layers, n_classes, dropout, rnn_type="gru").to(device)

# 가중치 초기화 적용
model.apply(init_weights)

# 5. 학습 데이터 준비 (카테고리 인코딩)
le = LabelEncoder()
y_labels = le.fit_transform([category for _, category in processed_news_data])  # 카테고리를 숫자로 변환
X_train = torch.tensor(padded_data, dtype=torch.long).to(device)
y_train = torch.tensor(y_labels, dtype=torch.long).to(device)

# 6. 클래스 가중치 계산 (y_labels가 정의된 이후)
class_weights = compute_class_weight('balanced', classes=np.unique(y_labels), y=y_labels)
class_weights = torch.tensor(class_weights, dtype=torch.float).to(device)

# 손실 함수 정의 (CrossEntropyLoss에 클래스 가중치 적용)
criterion = nn.CrossEntropyLoss(weight=class_weights).to(device)

# 옵티마이저 설정
optimizer = optim.Adam(model.parameters(), lr=0.001)  # Adam 옵티마이저 사용

# 학습률 스케줄러 설정 (ReduceLROnPlateau)
scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', patience=2, factor=0.1)

# 7. 학습/검증 데이터 분리 (셔플링 추가)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.2, random_state=42, shuffle=True)

# 8. 모델 학습 및 저장 루프
epochs = 15
batch_size = 128  # 배치 크기를 늘릴 수 있음 (하드웨어 성능에 따라 조절 가능)
patience = 5  # 조기 종료를 위한 patience 설정
best_val_loss = float('inf')
patience_counter = 0

# 모델과 옵티마이저 상태 저장할 경로
save_path = "rnn_category_model.pth"

for epoch in range(epochs):
    model.train()
    
    for i in range(0, len(X_train), batch_size):
        X_batch = X_train[i:i + batch_size]
        y_batch = y_train[i:i + batch_size]

        # 모델 예측
        outputs = model(X_batch)  # (배치 크기, 카테고리 수)

        # 손실 계산
        loss = criterion(outputs, y_batch)

        # 역전파 및 가중치 업데이트
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

    # 검증 데이터로 성능 평가
    model.eval()
    with torch.no_grad():
        val_outputs = model(X_val)
        val_predictions = torch.argmax(val_outputs, dim=1)  # 카테고리 예측
        val_loss = criterion(val_outputs, y_val)

        # 평가 지표 계산
        val_accuracy = accuracy_score(y_val.cpu().numpy(), val_predictions.cpu().numpy())
        val_f1 = f1_score(y_val.cpu().numpy(), val_predictions.cpu().numpy(), average='weighted')
        val_precision = precision_score(y_val.cpu().numpy(), val_predictions.cpu().numpy(), average='weighted')
        val_recall = recall_score(y_val.cpu().numpy(), val_predictions.cpu().numpy(), average='weighted')
        
        print(f'Epoch {epoch + 1}/{epochs}, Loss: {loss.item()}, Val Loss: {val_loss.item()}, Val Accuracy: {val_accuracy}, Val F1: {val_f1}, Precision: {val_precision}, Recall: {val_recall}')

        # 학습률 조정 (ReduceLROnPlateau에 맞게 검증 손실 사용)
        scheduler.step(val_loss)

        # 조기 종료 체크
        if val_loss.item() < best_val_loss:
            best_val_loss = val_loss.item()
            patience_counter = 0
            # 모델 저장
            torch.save({
                'epoch': epoch + 1,
                'model_state_dict': model.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'loss': loss.item(),
            }, save_path)
        else:
            patience_counter += 1

        if patience_counter >= patience:
            print("Early stopping")
            break

print("학습 완료 및 모델 저장 완료.")
